# Setup


In [ ]:
!pip install osmnet
!pip install matplotlib==3.1.3
!pip install pandana
!pip install folium
!pip install geopandas
!pip install rtree

     |████████████████████████████████| 1.0 MB 13.8 MB/s 
     |████████████████████████████████| 6.3 MB 34.7 MB/s 
     |████████████████████████████████| 15.4 MB 31.4 MB/s 
     |████████████████████████████████| 13.1 MB 6.4 MB/s 
  Attempting uninstall: matplotlib
    Found existing installation: matplotlib 3.2.2
    Uninstalling matplotlib-3.2.2:
      Successfully uninstalled matplotlib-3.2.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
albumentations 0.1.12 requires imgaug<0.2.7,>=0.2.5, but you have imgaug 0.2.9 which is incompatible.


     |████████████████████████████████| 1.7 MB 10.1 MB/s 
     |████████████████████████████████| 994 kB 8.1 MB/s 


In [ ]:
import numpy as np
import pandas as pd
import geopandas as gpd
from geopandas import datasets, GeoDataFrame, read_file
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
from sklearn.preprocessing import MinMaxScaler
import folium
import math


In [ ]:
file_id = '1gWf1-JUqdgjs55L2GrD1RdZQZENtUy2k' # URL id. 
%cd /content
!gdown --id 1gWf1-JUqdgjs55L2GrD1RdZQZENtUy2k -O response.json
#!unzip -j -qq dataset.zip -d dataset

/content
Downloading...
From: https://drive.google.com/uc?id=1gWf1-JUqdgjs55L2GrD1RdZQZENtUy2k
To: /content/response.json
100% 28.5M/28.5M [00:00<00:00, 250MB/s]


In [ ]:
!git clone https://github.com/CityScope/CSL_HCMC

Cloning into 'CSL_HCMC'...
remote: Enumerating objects: 1957, done.
remote: Counting objects: 100% (617/617), done.
remote: Compressing objects: 100% (336/336), done.
remote: Total 1957 (delta 323), reused 515 (delta 275), pack-reused 1340
Receiving objects: 100% (1957/1957), 179.17 MiB | 10.72 MiB/s, done.
Resolving deltas: 100% (1000/1000), done.
Checking out files: 100% (542/542), done.


# Step 0 (Hough Transform)

In [ ]:
#visualize
data = gpd.read_file("/content/response.json")
data = GeoDataFrame(data)
plot= data.plot(figsize=(500, 300))

In [ ]:
data = gpd.read_file("/content/response.json")

normalize_max = 250
scaler = MinMaxScaler((0, normalize_max))

X = np.array(data.geometry.y).reshape(-1, 1)
Y = np.array(data.geometry.x).reshape(-1, 1)

X = scaler.fit_transform(X).round(7)
Y = scaler.fit_transform(Y).round(7)

X = X.reshape(-1)
Y = Y.reshape(-1)

In [ ]:
def hough_line(X, Y):
  # Rho and Theta ranges
  thetas = np.deg2rad(np.arange(-90.0, 90.0, 0.5))
  width = normalize_max
  height = normalize_max
  diag_len = int(round(math.sqrt(width * width + height * height)))
  rhos = np.linspace(-diag_len, diag_len, 2 * diag_len)

  # Save some resuable values
  cos_t = np.cos(thetas)
  sin_t = np.sin(thetas)
  num_thetas = len(thetas)

  # Hough accumulator array of theta vs rho
  accumulator = np.zeros((2 * diag_len, num_thetas), dtype=np.uint64)
  y_idxs, x_idxs = (Y, X)  # (row, col) indexes to edges

  # Vote in the hough accumulator
  for i in range(len(x_idxs)):
    x = x_idxs[i]
    y = y_idxs[i]

    for t_idx in range(num_thetas):
      # Calculate rho. diag_len is added for a positive index
      rho = round(x * cos_t[t_idx] + y * sin_t[t_idx]) + diag_len
      accumulator[rho, t_idx] += 1
  return accumulator, thetas, rhos, diag_len

In [ ]:
accumulator, thetas, rhos, diag_len = hough_line(X, Y)

In [ ]:
_accumulator = np.array(accumulator)

filter = np.zeros(len(data))
width = normalize_max
height = normalize_max
number_line_detect = []

i = 0
while i < 3:
  if np.max(_accumulator) <= 0:
    break
  idx = np.argmax(_accumulator)
  # rho = rhos[idx // _accumulator.shape[1]]
  theta = thetas[idx % _accumulator.shape[1]]

  count = 0
  if theta not in [np.pi/2, -np.pi/2]:
    for j in range(len(X)):
      rho_ = round(X[j] * np.cos(theta) + Y[j] * np.sin(theta)) + diag_len
      if rho_ == idx // _accumulator.shape[1] and filter[j] not in number_line_detect:
        count += 1

  if count > 9000:
    number_line_detect.append(i+1)
    for j in range(len(X)):
      rho_ = round(X[j] * np.cos(theta) + Y[j] * np.sin(theta)) + diag_len
      if rho_ == idx // _accumulator.shape[1] and filter[j] not in number_line_detect:
        filter[j] = i+1
  else:
    i -= 1

  _accumulator[idx // _accumulator.shape[1]][idx % _accumulator.shape[1]] = 0
  i += 1

In [ ]:
data['filter'] = filter
new_data = data[data['filter'] == 0]
fig, ax = plt.subplots(figsize = (100,100)) 
data.plot(color = 'blue',ax=ax)
new_data.plot(color = 'red',ax=ax)

# Step 1 (Prepare Data)

In [ ]:
district = gpd.read_file("/content/CSL_HCMC/Data/GIS/Population/population_HCMC/population_shapefile/Population_District_Level.shp")
point_click = new_data

In [ ]:
district['population_growth_speed'] = district.Pop_2019 / district.Pop_2017
district = district.sort_values(by='population_growth_speed', ascending=False)
top_district = district
top_district = top_district[['Dist_Name', 'Shape_Leng', 'Shape_Area', 'geometry']]

In [ ]:
_point_click = point_click.to_crs('epsg:3857')
_top_district = top_district.to_crs('epsg:3857')

In [ ]:
send_point_to_District = gpd.sjoin(_point_click, _top_district)

In [ ]:
point_in_district = [send_point_to_District[send_point_to_District.Dist_Name == dist_name][['geometry', 'Dist_Name']] for dist_name in top_district.Dist_Name]

In [ ]:
point_in_district[0].head()

geometry   Dist_Name
143   POINT (11893078.813 1215549.134)  District 9
200   POINT (11890271.825 1216812.741)  District 9
630   POINT (11895191.117 1213529.631)  District 9
874   POINT (11888254.950 1211172.574)  District 9
1169  POINT (11890037.725 1217223.846)  District 9

In [ ]:
len(point_in_district)

24

# Step 2 (Clustering)

In [ ]:
Kmeans = KMeans(n_clusters=30)
scaler = MinMaxScaler()
top_cluster = []

In [ ]:
def sortSecond(val):
    return val[1]

for i in range(24):
  # Normalize
  X = np.array(point_in_district[i].geometry.x).reshape((-1, 1))
  Y = np.array(point_in_district[i].geometry.y).reshape((-1, 1))

  X = scaler.fit_transform(X)
  Y = scaler.fit_transform(Y)

  # Clustering
  points = np.hstack((X,Y))
  labels = Kmeans.fit_predict(points)
  point_in_district[i]['label'] = labels

  # Find top
  sizeOfCluster = []
  for i in range(30):
    sizeOfCluster.append((i, len(labels[labels==i])))
  sizeOfCluster.sort(key=sortSecond)

  top_cluster.append(sizeOfCluster[-1][0])

In [ ]:
point_in_district[0].head()

geometry   Dist_Name  label
143   POINT (11893078.813 1215549.134)  District 9      6
200   POINT (11890271.825 1216812.741)  District 9      1
630   POINT (11895191.117 1213529.631)  District 9      2
874   POINT (11888254.950 1211172.574)  District 9     10
1169  POINT (11890037.725 1217223.846)  District 9      1

In [ ]:
len(point_in_district)

24

# Step 3 (Visualize Data)

In [ ]:
from folium import plugins

In [ ]:
map = folium.Map(location = [10.81822, 106.77435], tiles='OpenStreetMap' , zoom_start = 11)

In [ ]:
for i in range(24):
  cluster_to_draw = point_in_district[i][point_in_district[i].label == top_cluster[i]]
  cluster_to_draw = cluster_to_draw.to_crs('epsg:4326')

  data = [[point.xy[1][0], point.xy[0][0]] for point in cluster_to_draw.geometry]
  plugins.HeatMap(data).add_to(map)

In [ ]:
map